In [25]:
import pandas as pd
dataset1 = pd.read_table('PET.txt')
type(dataset1)

pandas.core.frame.DataFrame

In [26]:
dataset1.shape

(180159, 1)

In [27]:
dataset1.iloc[0,0]

'{"series_id":"PET.EMM_EPMM_PTE_R1Z_DPG.W","name":"Lower Atlantic (PADD 1C) Midgrade All Formulations Retail Gasoline Prices, Weekly","units":"Dollars per Gallon","f":"W","unitsshort":"$\\/gal","description":"Lower Atlantic (PADD 1C) Midgrade All Formulations Retail Gasoline Prices","copyright":"None","source":"EIA, U.S. Energy Information Administration","geography":"USA-FL+USA-GA+USA-NC+USA-SC+USA-VA+USA-WV","start":"19941128","end":"20181112","last_updated":"2018-11-13T16:11:04-05:00","data":[["20181112",2.846],["20181105",2.897],["20181029",2.958],["20181022",3.002],["20181015",3.039],["20181008",3.054],["20181001",3.016],["20180924",2.968],["20180917",2.977],["20180910",2.98],["20180903",2.968],["20180827",2.955],["20180820",2.971],["20180813",3.006],["20180806",2.994],["20180730",2.985],["20180723",2.967],["20180716",2.996],["20180709",2.965],["20180702",2.956],["20180625",2.949],["20180618",2.991],["20180611",3.027],["20180604",3.079],["20180528",3.106],["20180521",3.045],["2018

Bacially, each '{...}' is a dict-like array, but in case that true, null and other data type objects exist(which indeed happen in the PET file), we use json to load and convert the data into the form we like, that is pandas dataframe

In [28]:
import json
a = json.loads(dataset1.iloc[0,0])
a

{'series_id': 'PET.EMM_EPMM_PTE_R1Z_DPG.W',
 'name': 'Lower Atlantic (PADD 1C) Midgrade All Formulations Retail Gasoline Prices, Weekly',
 'units': 'Dollars per Gallon',
 'f': 'W',
 'unitsshort': '$/gal',
 'description': 'Lower Atlantic (PADD 1C) Midgrade All Formulations Retail Gasoline Prices',
 'copyright': 'None',
 'source': 'EIA, U.S. Energy Information Administration',
 'geography': 'USA-FL+USA-GA+USA-NC+USA-SC+USA-VA+USA-WV',
 'start': '19941128',
 'end': '20181112',
 'last_updated': '2018-11-13T16:11:04-05:00',
 'data': [['20181112', 2.846],
  ['20181105', 2.897],
  ['20181029', 2.958],
  ['20181022', 3.002],
  ['20181015', 3.039],
  ['20181008', 3.054],
  ['20181001', 3.016],
  ['20180924', 2.968],
  ['20180917', 2.977],
  ['20180910', 2.98],
  ['20180903', 2.968],
  ['20180827', 2.955],
  ['20180820', 2.971],
  ['20180813', 3.006],
  ['20180806', 2.994],
  ['20180730', 2.985],
  ['20180723', 2.967],
  ['20180716', 2.996],
  ['20180709', 2.965],
  ['20180702', 2.956],
  ['2018

In [1]:
def check(output):
    import json
    not_json = []
    no_start_with_data = []
    start_lens = []
    name_list = []
    for i in range(output.shape[0]):
        try:
            temp = json.loads(output.iloc[i,0])
            if 'data' not in temp.keys():
                if 'start' in temp.keys():
                    no_start_with_data.append(i)
            else:
                temp_len = len(temp['start'])
                temp['series_id']
                name_list.append(temp['name'])
                temp['units']
                if temp_len not in start_lens:
                    start_lens.append(temp_len)
                    print(temp['start'])
                    print(i)

        except:
            not_json.append(i)
    return not_json,no_start_with_data,start_lens, name_list



In [ ]:
not_json, no_start_with_data, start_lens, name_list = check(dataset1)

print(len(not_json))
print(len(no_start_with_data))
print(start_lens)

In [31]:
name_list = pd.Series(name_list)
name_list = name_list.apply(lambda x: x.split(',')[-1].strip())
name_list.unique()

array(['Weekly', 'Daily', '4 Week Avg', 'Monthly', 'Annual'], dtype=object)

In [43]:
name_list[name_list == '4 Week Avg'].shape

(431,)

There are three types of date format:

    1. Daily, Weekly, 4 Week Avg: "%Y%m%d" --> "%Y%m%d", convert it to itself
    2. Monthly: "%Y%m" --> "%Y%m%lastdayof%m" , for dates with only month, convert it to the last day of the regarding month
    3. Annual: "%Y" --> "%Y%12%31, for dates with only year, convert it to the end of the year
    



In [3]:
import datetime
def last_day_of_month(any_day):
    next_month = any_day.replace(day=28) + datetime.timedelta(days=4)  # this will never fail
    return next_month - datetime.timedelta(days=next_month.day)

def last_day_of_year(any_year):
    return any_year.replace(month=12,day=31)

The function below, constructRawData, is to grasp key information in the PET.txt file and generate four outputs:

    1. output_list_daily: a list whose elements are a dataframes with daily time-series index and one feature column
    2. output_list_weekly: a list whose elements are a weekly or 4 week avg time-series index
    3. output_list_month: a list whose elements are a dataframes with monthly time-series index and one feature column
    4. output_list_year: a list whose elements are dataframes with annually time-series index and one feature column
    5. id_name_dict: a dict storing description, frequency and units for each feature above

In [2]:
def constructRawData(datafile):
    N = datafile.shape[0]
    output_list_daily = []
    output_list_weekly = []
    output_list_month = []
    output_list_qtr = []
    output_list_year = []
    id_name_dict = {}
    
    import json
    for i in range(N):
        temp = json.loads(datafile.iloc[i,0])
        if 'data' in temp.keys():
            temp_id = temp['series_id']
            temp_name = temp['name']
            temp_data = temp['data']
            temp_units = temp['units']
            temp_freq = temp_name.split(',')[-1].strip()
            id_name_dict[temp_id] = [temp_name,temp_units,temp_freq]  # save id, name, units, and frequency accordingly
            temp_df = pd.DataFrame(temp_data,columns=['Date',temp_id])
            
            if temp_freq == 'Daily':
                temp_df['Date'] = pd.Series(pd.to_datetime(temp_df['Date'],format='%Y%m%d'))
                temp_df.set_index('Date',inplace=True)
                temp_df.sort_index(ascending=True,inplace=True)
                output_list_daily.append(temp_df)
                
            elif temp_freq == 'Weekly' or temp_freq == '4 Week Avg':
                temp_df['Date'] = pd.Series(pd.to_datetime(temp_df['Date'],format='%Y%m%d'))
                temp_df.set_index('Date',inplace=True)
                temp_df.sort_index(ascending=True,inplace=True)
                output_list_weekly.append(temp_df)
                
            elif temp_freq == 'Monthly':
                temp_df['Date'] = pd.Series(pd.to_datetime(temp_df['Date'],format='%Y%m'))
                temp_df['Date'] = temp_df['Date'].apply(last_day_of_month)
                temp_df.set_index('Date',inplace=True)
                temp_df.sort_index(ascending=True,inplace=True)
                output_list_month.append(temp_df)
            
            elif temp_freq == 'Quarterly':
                temp_df['Date'] = pd.Series(pd.to_datetime(temp_df['Date']))
                temp_df['Date'] = temp_df['Date'].apply(last_day_of_quarter)
                temp_df.set_index('Date',inplace=True)
                temp_df.sort_index(ascending=True,inplace=True)
                output_list_qtr.append(temp_df)    
            
            else:
                temp_df['Date'] = pd.Series(pd.to_datetime(temp_df['Date'],format='%Y'))
                temp_df['Date'] = temp_df['Date'].apply(last_day_of_year)
                temp_df.set_index('Date',inplace=True)
                temp_df.sort_index(ascending=True,inplace=True)
                output_list_year.append(temp_df)

            print(str(i)+'th element is saved')
        else:
            print(str(i)+'th element is identified as No Data')

    return output_list_daily,output_list_weekly,output_list_month,output_list_qtr, output_list_year,id_name_dict
    

In [49]:
PET_raw_day, PET_raw_week, PET_raw_month, PET_raw_qtr, PET_raw_year, PET_id_dict = constructRawData(dataset1)

0th element is saved
1th element is saved
2th element is saved
3th element is saved
4th element is saved
5th element is saved
6th element is saved
7th element is saved
8th element is saved
9th element is saved
10th element is saved
11th element is saved
12th element is saved
13th element is saved
14th element is saved
15th element is saved
16th element is saved
17th element is saved
18th element is saved
19th element is saved
20th element is saved
21th element is saved
22th element is saved
23th element is saved
24th element is saved
25th element is saved
26th element is saved
27th element is saved
28th element is saved
29th element is saved
30th element is saved
31th element is saved
32th element is saved
33th element is saved
34th element is saved
35th element is saved
36th element is saved
37th element is saved
38th element is saved
39th element is saved
40th element is saved
41th element is saved
42th element is saved
43th element is saved
44th element is saved
45th element is save

423th element is saved
424th element is saved
425th element is saved
426th element is saved
427th element is saved
428th element is saved
429th element is saved
430th element is saved
431th element is saved
432th element is saved
433th element is saved
434th element is saved
435th element is saved
436th element is saved
437th element is saved
438th element is saved
439th element is saved
440th element is saved
441th element is saved
442th element is saved
443th element is saved
444th element is saved
445th element is saved
446th element is saved
447th element is saved
448th element is saved
449th element is saved
450th element is saved
451th element is saved
452th element is saved
453th element is saved
454th element is saved
455th element is saved
456th element is saved
457th element is saved
458th element is saved
459th element is saved
460th element is saved
461th element is saved
462th element is saved
463th element is saved
464th element is saved
465th element is saved
466th eleme

820th element is saved
821th element is saved
822th element is saved
823th element is saved
824th element is saved
825th element is saved
826th element is saved
827th element is saved
828th element is saved
829th element is saved
830th element is saved
831th element is saved
832th element is saved
833th element is saved
834th element is saved
835th element is saved
836th element is saved
837th element is saved
838th element is saved
839th element is saved
840th element is saved
841th element is saved
842th element is saved
843th element is saved
844th element is saved
845th element is saved
846th element is saved
847th element is saved
848th element is saved
849th element is saved
850th element is saved
851th element is saved
852th element is saved
853th element is saved
854th element is saved
855th element is saved
856th element is saved
857th element is saved
858th element is saved
859th element is saved
860th element is saved
861th element is saved
862th element is saved
863th eleme

1202th element is saved
1203th element is saved
1204th element is saved
1205th element is saved
1206th element is saved
1207th element is saved
1208th element is saved
1209th element is saved
1210th element is saved
1211th element is saved
1212th element is saved
1213th element is saved
1214th element is saved
1215th element is saved
1216th element is saved
1217th element is saved
1218th element is saved
1219th element is saved
1220th element is saved
1221th element is saved
1222th element is saved
1223th element is saved
1224th element is saved
1225th element is saved
1226th element is saved
1227th element is saved
1228th element is saved
1229th element is saved
1230th element is saved
1231th element is saved
1232th element is saved
1233th element is saved
1234th element is saved
1235th element is saved
1236th element is saved
1237th element is saved
1238th element is saved
1239th element is saved
1240th element is saved
1241th element is saved
1242th element is saved
1243th element i

1583th element is saved
1584th element is saved
1585th element is saved
1586th element is saved
1587th element is saved
1588th element is saved
1589th element is saved
1590th element is saved
1591th element is saved
1592th element is saved
1593th element is saved
1594th element is saved
1595th element is saved
1596th element is saved
1597th element is saved
1598th element is saved
1599th element is saved
1600th element is saved
1601th element is saved
1602th element is saved
1603th element is saved
1604th element is saved
1605th element is saved
1606th element is saved
1607th element is saved
1608th element is saved
1609th element is saved
1610th element is saved
1611th element is saved
1612th element is saved
1613th element is saved
1614th element is saved
1615th element is saved
1616th element is saved
1617th element is saved
1618th element is saved
1619th element is saved
1620th element is saved
1621th element is saved
1622th element is saved
1623th element is saved
1624th element i

...

170435th element is identified as No Data
170436th element is identified as No Data
170437th element is identified as No Data
170438th element is identified as No Data
170439th element is identified as No Data
170440th element is identified as No Data
170441th element is identified as No Data
170442th element is identified as No Data
170443th element is identified as No Data
170444th element is identified as No Data
170445th element is identified as No Data
170446th element is identified as No Data
170447th element is identified as No Data
170448th element is identified as No Data
170449th element is identified as No Data
170450th element is identified as No Data
170451th element is identified as No Data
170452th element is identified as No Data
170453th element is identified as No Data
170454th element is identified as No Data
170455th element is identified as No Data
170456th element is identified as No Data
170457th element is identified as No Data
170458th element is identified as 

172434th element is identified as No Data
172435th element is identified as No Data
172436th element is identified as No Data
172437th element is identified as No Data
172438th element is identified as No Data
172439th element is identified as No Data
172440th element is identified as No Data
172441th element is identified as No Data
172442th element is identified as No Data
172443th element is identified as No Data
172444th element is identified as No Data
172445th element is identified as No Data
172446th element is identified as No Data
172447th element is identified as No Data
172448th element is identified as No Data
172449th element is identified as No Data
172450th element is identified as No Data
172451th element is identified as No Data
172452th element is identified as No Data
172453th element is identified as No Data
172454th element is identified as No Data
172455th element is identified as No Data
172456th element is identified as No Data
172457th element is identified as 

174434th element is identified as No Data
174435th element is identified as No Data
174436th element is identified as No Data
174437th element is identified as No Data
174438th element is identified as No Data
174439th element is identified as No Data
174440th element is identified as No Data
174441th element is identified as No Data
174442th element is identified as No Data
174443th element is identified as No Data
174444th element is identified as No Data
174445th element is identified as No Data
174446th element is identified as No Data
174447th element is identified as No Data
174448th element is identified as No Data
174449th element is identified as No Data
174450th element is identified as No Data
174451th element is identified as No Data
174452th element is identified as No Data
174453th element is identified as No Data
174454th element is identified as No Data
174455th element is identified as No Data
174456th element is identified as No Data
174457th element is identified as 

176433th element is identified as No Data
176434th element is identified as No Data
176435th element is identified as No Data
176436th element is identified as No Data
176437th element is identified as No Data
176438th element is identified as No Data
176439th element is identified as No Data
176440th element is identified as No Data
176441th element is identified as No Data
176442th element is identified as No Data
176443th element is identified as No Data
176444th element is identified as No Data
176445th element is identified as No Data
176446th element is identified as No Data
176447th element is identified as No Data
176448th element is identified as No Data
176449th element is identified as No Data
176450th element is identified as No Data
176451th element is identified as No Data
176452th element is identified as No Data
176453th element is identified as No Data
176454th element is identified as No Data
176455th element is identified as No Data
176456th element is identified as 

178909th element is identified as No Data
178910th element is identified as No Data
178911th element is identified as No Data
178912th element is identified as No Data
178913th element is identified as No Data
178914th element is identified as No Data
178915th element is identified as No Data
178916th element is identified as No Data
178917th element is identified as No Data
178918th element is identified as No Data
178919th element is identified as No Data
178920th element is identified as No Data
178921th element is identified as No Data
178922th element is identified as No Data
178923th element is identified as No Data
178924th element is identified as No Data
178925th element is identified as No Data
178926th element is identified as No Data
178927th element is identified as No Data
178928th element is identified as No Data
178929th element is identified as No Data
178930th element is identified as No Data
178931th element is identified as No Data
178932th element is identified as 

In [50]:
print(len(PET_raw_day))
print(len(PET_raw_week))
print(len(PET_raw_month))
print(len(PET_raw_qtr))
print(len(PET_raw_year))
print(len(PET_id_dict))

31
1554
77317
87176
166078


In [51]:
PET_raw_day_all = pd.DataFrame().join(PET_raw_day,how='outer')

In [52]:
PET_raw_day_all.shape

(9923, 31)

In [54]:
PET_raw_day_all.to_pickle("PET_raw_day_all.pkl")

In [55]:
raw_data_day_all_read = pd.read_pickle("PET_raw_day_all.pkl")
raw_data_day_all_read.shape

(9923, 31)

In [56]:
raw_data_day_all_read.iloc[:10,:20]

PET.RCLC3.D  PET.RCLC4.D  PET.RWTC.D  PET.RBRTE.D  PET.RCLC1.D  \
Date                                                                         
1980-01-02          NaN          NaN         NaN          NaN          NaN   
1980-01-03          NaN          NaN         NaN          NaN          NaN   
1980-01-04          NaN          NaN         NaN          NaN          NaN   
1980-01-07          NaN          NaN         NaN          NaN          NaN   
1980-01-08          NaN          NaN         NaN          NaN          NaN   
1980-01-09          NaN          NaN         NaN          NaN          NaN   
1980-01-10          NaN          NaN         NaN          NaN          NaN   
1980-01-11          NaN          NaN         NaN          NaN          NaN   
1980-01-14          NaN          NaN         NaN          NaN          NaN   
1980-01-15          NaN          NaN         NaN          NaN          NaN   

            PET.RCLC2.D  PET.EER_EPJK_PF4_RGC_DPG.D  \
Date                                                  
1980-01-02          NaN                         NaN   
1980-01-03          NaN                         NaN   
1980-01-04          NaN                         NaN   
1980-01-07          NaN                         NaN   
1980-01-08          NaN                         NaN   
1980-01-09          NaN                         NaN   
1980-01-10          NaN                         NaN   
1980-01-11          NaN                         NaN   
1980-01-14          NaN                         NaN   
1980-01-15          NaN                         NaN   

            PET.EER_EPMRU_PF4_RGC_DPG.D  PET.EER_EPD2DXL0_PF4_Y35NY_DPG.D  \
Date                                                                        
1980-01-02                          NaN                               NaN   
1980-01-03                          NaN                               NaN   
1980-01-04                          NaN                               NaN   
1980-01-07                          NaN                               NaN   
1980-01-08                          NaN                               NaN   
1980-01-09                          NaN                               NaN   
1980-01-10                          NaN                               NaN   
1980-01-11                          NaN                               NaN   
1980-01-14                          NaN                               NaN   
1980-01-15                          NaN                               NaN   

            PET.EER_EPD2F_PE1_Y35NY_DPG.D  PET.EER_EPD2F_PE2_Y35NY_DPG.D  \
Date                                                                       
1980-01-02                          0.821                            NaN   
1980-01-03                          0.827                            NaN   
1980-01-04                          0.850                            NaN   
1980-01-07                          0.828                            NaN   
1980-01-08                          0.786                            NaN   
1980-01-09                          0.792                            NaN   
1980-01-10                          0.798                            NaN   
1980-01-11                          0.776                            NaN   
1980-01-14                          0.758                            NaN   
1980-01-15                          0.750                            NaN   

            PET.EER_EPD2F_PE3_Y35NY_DPG.D  PET.EER_EPLLPA_PF4_Y44MB_DPG.D  \
Date                                                                        
1980-01-02                          0.890                             NaN   
1980-01-03                          0.866                             NaN   
1980-01-04                          0.880                             NaN   
1980-01-07                          0.879                             NaN   
1980-01-08                          0.859                             NaN   
1980-01-09                          0

In [57]:
raw_data_day_all_read.index.is_unique

True

In [58]:
PET_raw_week_all = pd.DataFrame().join(PET_raw_week,how='outer')
PET_raw_week_all.shape

(3501, 1554)

In [59]:
PET_raw_week_all.to_pickle("PET_raw_week_all.pkl")

In [60]:
raw_data_week_all_read = pd.read_pickle("PET_raw_week_all.pkl")
raw_data_week_all_read.shape

(3501, 1554)

In [62]:
raw_data_week_all_read.index.is_unique

True

In [63]:
PET_raw_month_all = pd.DataFrame().join(PET_raw_month,how='outer')
PET_raw_month_all.shape

(1186, 77317)

In [64]:
PET_raw_month_all.to_pickle("PET_raw_month_all.pkl")

In [67]:
PET_raw_year_all = pd.DataFrame().join(PET_raw_year,how='outer')
PET_raw_year_all.shape

(160, 87176)

In [75]:
PET_raw_year_all.to_pickle("PET_raw_year_all.pkl")

In [70]:
print(PET_raw_day_all.info())
print('----------------------------------------------------------')
print(PET_raw_week_all.info())
print('----------------------------------------------------------')
print(PET_raw_month_all.info())
print('----------------------------------------------------------')
print(PET_raw_year_all.info())
print('----------------------------------------------------------')

<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 9923 entries, 1980-01-02 to 2018-11-06
Data columns (total 31 columns):
PET.RCLC3.D                         8940 non-null float64
PET.RCLC4.D                         8499 non-null float64
PET.RWTC.D                          8285 non-null float64
PET.RBRTE.D                         7991 non-null float64
PET.RCLC1.D                         8936 non-null float64
PET.RCLC2.D                         8499 non-null float64
PET.EER_EPJK_PF4_RGC_DPG.D          7200 non-null float64
PET.EER_EPMRU_PF4_RGC_DPG.D         8163 non-null float64
PET.EER_EPD2DXL0_PF4_Y35NY_DPG.D    3129 non-null float64
PET.EER_EPD2F_PE1_Y35NY_DPG.D       9744 non-null float64
PET.EER_EPD2F_PE2_Y35NY_DPG.D       6206 non-null float64
PET.EER_EPD2F_PE3_Y35NY_DPG.D       9748 non-null float64
PET.EER_EPLLPA_PF4_Y44MB_DPG.D      6617 non-null float64
PET.EER_EPD2DC_PF4_Y05LA_DPG.D      5671 non-null float64
PET.EER_EPD2DXL0_PF4_RGC_DPG.D      3129 non-null float64
PET.E

In [72]:
a = pd.DataFrame(PET_id_dict).T
a['name'] = a[0]
a['units'] = a[1]
a['frequency'] = a[2]
a.head()

0  \
PET.EMM_EPMM_PTE_R1Z_DPG.W  Lower Atlantic (PADD 1C) Midgrade All Formulat...   
PET.EMM_EPMM_PTE_R20_DPG.W  Midwest Midgrade All Formulations Retail Gasol...   
PET.EMM_EPMM_PTE_SCA_DPG.W  California Midgrade All Formulations Retail Ga...   
PET.EMM_EPM0_PTE_SMN_DPG.W  Minnesota All Grades All Formulations Retail G...   
PET.EMM_EPMP_PTE_SFL_DPG.W  Florida Premium All Formulations Retail Gasoli...   

                                             1       2  \
PET.EMM_EPMM_PTE_R1Z_DPG.W  Dollars per Gallon  Weekly   
PET.EMM_EPMM_PTE_R20_DPG.W  Dollars per Gallon  Weekly   
PET.EMM_EPMM_PTE_SCA_DPG.W  Dollars per Gallon  Weekly   
PET.EMM_EPM0_PTE_SMN_DPG.W  Dollars per Gallon  Weekly   
PET.EMM_EPMP_PTE_SFL_DPG.W  Dollars per Gallon  Weekly   

                                                                         name  \
PET.EMM_EPMM_PTE_R1Z_DPG.W  Lower Atlantic (PADD 1C) Midgrade All Formulat...   
PET.EMM_EPMM_PTE_R20_DPG.W  Midwest Midgrade All Formulations Retail Gasol...   
PET.EMM_EPMM_PTE_SCA_DPG.W  California Midgrade All Formulations Retail Ga...   
PET.EMM_EPM0_PTE_SMN_DPG.W  Minnesota All Grades All Formulations Retail G...   
PET.EMM_EPMP_PTE_SFL_DPG.W  Florida Premium All Formulations Retail Gasoli...   

                                         units frequency  
PET.EMM_EPMM_PTE_R1Z_DPG.W  Dollars per Gallon    Weekly  
PET.EMM_EPMM_PTE_R20_DPG.W  Dollars per Gallon    Weekly  
PET.EMM_EPMM_PTE_SCA_DPG.W  Dollars per Gallon    Weekly  
PET.EMM_EPM0_PTE_SMN_DPG.W  Dollars per Gallon    Weekly  
PET.EMM_EPMP_PTE_SFL_DPG.W  Dollars per Gallon    Weekly

In [73]:
a.drop(columns=[0,1,2],inplace=True)
a.head()

name  \
PET.EMM_EPMM_PTE_R1Z_DPG.W  Lower Atlantic (PADD 1C) Midgrade All Formulat...   
PET.EMM_EPMM_PTE_R20_DPG.W  Midwest Midgrade All Formulations Retail Gasol...   
PET.EMM_EPMM_PTE_SCA_DPG.W  California Midgrade All Formulations Retail Ga...   
PET.EMM_EPM0_PTE_SMN_DPG.W  Minnesota All Grades All Formulations Retail G...   
PET.EMM_EPMP_PTE_SFL_DPG.W  Florida Premium All Formulations Retail Gasoli...   

                                         units frequency  
PET.EMM_EPMM_PTE_R1Z_DPG.W  Dollars per Gallon    Weekly  
PET.EMM_EPMM_PTE_R20_DPG.W  Dollars per Gallon    Weekly  
PET.EMM_EPMM_PTE_SCA_DPG.W  Dollars per Gallon    Weekly  
PET.EMM_EPM0_PTE_SMN_DPG.W  Dollars per Gallon    Weekly  
PET.EMM_EPMP_PTE_SFL_DPG.W  Dollars per Gallon    Weekly

In [74]:
a.to_pickle('PET_id_dict.pkl')

In [4]:
import pandas as pd
dataset2 = pd.read_table("STEO.txt")
dataset2.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4118 entries, 0 to 4117
Data columns (total 1 columns):
{"series_id":"STEO.JFPSPUS.A","name":"Jet Fuel Inventory, Annual","units":"million barrels, end-of-period","f":"A","copyright":"None","source":"U.S. Energy Information Administration (EIA) - Short Term Energy Outlook","geography":"USA","start":"1990","end":"2019","lastHistoricalPeriod":"2017","last_updated":"2018-11-06T12:01:05-05:00","data":[["2019",42.34797],["2018",41.59551],["2017",41.304],["2016",43.01],["2015",40.39],["2014",38.274],["2013",37.183],["2012",39.62],["2011",41.483],["2010",43.218],["2009",43.397],["2008",37.969],["2007",39.458],["2006",39.129],["2005",41.741],["2004",40.086],["2003",38.784000397],["2002",39.179000854],["2001",41.952999115],["2000",44.518001556],["1999",40.500999451],["1998",44.694000244],["1997",44.042999268],["1996",39.865001678],["1995",40.011001587],["1994",46.807998657],["1993",40.391998291],["1992",43.067001343],["1991",48.806999207],["1990

In [5]:
dataset2.iloc[0,0]

'{"series_id":"STEO.RFCOPUS.A","name":"Industrial Sector Generation from Residual Fuel Oil, Annual","units":"billion kilowatthours per day","f":"A","copyright":"None","source":"U.S. Energy Information Administration (EIA) - Short Term Energy Outlook","geography":"USA","start":"1990","end":"2019","lastHistoricalPeriod":"2017","last_updated":"2018-11-06T12:01:05-05:00","data":[["2019",0.00042055947671],["2018",0.0004855529726],["2017",0.00040380930685],["2016",0.00034328398907],["2015",0.00045135482192],["2014",0.00060484884932],["2013",0.00061277019178],["2012",0.00063597081967],["2011",0.00098554468493],["2010",0.0012154596986],["2009",0.0022560629041],["2008",0.0029389169672],["2007",0.0046270789589],["2006",0.0053267024932],["2005",0.0074488895616],["2004",0.0075892665847],["2003",0.0065474303836],["2002",0.0062716466027],["2001",0.0079896136185],["2000",0.0077998108561],["1999",0.0085689810471],["1998",0.009880249713],["1997",0.0091248656056],["1996",0.0098978180335],["1995",0.01011

In [6]:
not_json, no_start_with_data, start_lens, name_list = check(dataset2)

print(len(not_json))
print(len(no_start_with_data))
print(start_lens)

1990
0
199001
1181
0
0
[4, 6]


In [7]:
import json
json.loads(dataset2.iloc[1181,0])

{'series_id': 'STEO.CGSP_ENC.M',
 'name': 'Real Gross State Product E. N. Central, Monthly',
 'units': 'billion chained 2009 dollars (seasonally-adjusted annual rate)',
 'f': 'M',
 'description': 'Census division includes States of IL, IN, MI, OH, and WI',
 'copyright': 'None',
 'source': 'U.S. Energy Information Administration (EIA) - Short Term Energy Outlook',
 'geography': 'USA-IL+USA-IN+USA-MI+USA-OH+USA-WI',
 'start': '199001',
 'end': '201912',
 'lastHistoricalPeriod': '201803',
 'last_updated': '2018-11-06T12:01:05-05:00',
 'data': [['201912', 2480.181],
  ['201911', 2477.165],
  ['201910', 2474.007],
  ['201909', 2470.748],
  ['201908', 2467.276],
  ['201907', 2463.632],
  ['201906', 2459.836],
  ['201905', 2455.833],
  ['201904', 2451.642],
  ['201903', 2446.827],
  ['201902', 2442.589],
  ['201901', 2438.49],
  ['201812', 2435.103],
  ['201811', 2430.856],
  ['201810', 2426.3208825],
  ['201809', 2421.5909121],
  ['201808', 2416.4085836],
  ['201807', 2410.8675802],
  ['2018

In [8]:
name_list = pd.Series(name_list)
name_list = name_list.apply(lambda x: x.split(',')[-1].strip())
name_list.unique()

array(['Annual', 'Monthly', 'Quarterly'], dtype=object)

In [9]:
pd.to_datetime('2011Q2').replace(month=pd.to_datetime('2011Q2').month+3) - datetime.timedelta(1)

Timestamp('2011-06-30 00:00:00')

In [11]:
def last_day_of_quarter(any_qtr):
    month_rep = any_qtr.month + 3
    if month_rep <= 12:
        return any_qtr.replace(month=month_rep) - datetime.timedelta(1)
    else:
        return any_qtr.replace(month=12,day=31)

In [12]:
last_day_of_quarter(pd.to_datetime('2011Q4'))

Timestamp('2011-12-31 00:00:00')

In [13]:
STEO_raw_day, STEO_raw_week, STEO_raw_month, STEO_raw_qtr, STEO_raw_year, STEO_id_dict = constructRawData(dataset2)

0th element is saved
1th element is saved
2th element is saved
3th element is saved
4th element is saved
5th element is saved
6th element is saved
7th element is saved
8th element is saved
9th element is saved
10th element is saved
11th element is saved
12th element is saved
13th element is saved
14th element is saved
15th element is saved
16th element is saved
17th element is saved
18th element is saved
19th element is saved
20th element is saved
21th element is saved
22th element is saved
23th element is saved
24th element is saved
25th element is saved
26th element is saved
27th element is saved
28th element is saved
29th element is saved
30th element is saved
31th element is saved
32th element is saved
33th element is saved
34th element is saved
35th element is saved
36th element is saved
37th element is saved
38th element is saved
39th element is saved
40th element is saved
41th element is saved
42th element is saved
43th element is saved
44th element is saved
45th element is save

412th element is saved
413th element is saved
414th element is saved
415th element is saved
416th element is saved
417th element is saved
418th element is saved
419th element is saved
420th element is saved
421th element is saved
422th element is saved
423th element is saved
424th element is saved
425th element is saved
426th element is saved
427th element is saved
428th element is saved
429th element is saved
430th element is saved
431th element is saved
432th element is saved
433th element is saved
434th element is saved
435th element is saved
436th element is saved
437th element is saved
438th element is saved
439th element is saved
440th element is saved
441th element is saved
442th element is saved
443th element is saved
444th element is saved
445th element is saved
446th element is saved
447th element is saved
448th element is saved
449th element is saved
450th element is saved
451th element is saved
452th element is saved
453th element is saved
454th element is saved
455th eleme

838th element is saved
839th element is saved
840th element is saved
841th element is saved
842th element is saved
843th element is saved
844th element is saved
845th element is saved
846th element is saved
847th element is saved
848th element is saved
849th element is saved
850th element is saved
851th element is saved
852th element is saved
853th element is saved
854th element is saved
855th element is saved
856th element is saved
857th element is saved
858th element is saved
859th element is saved
860th element is saved
861th element is saved
862th element is saved
863th element is saved
864th element is saved
865th element is saved
866th element is saved
867th element is saved
868th element is saved
869th element is saved
870th element is saved
871th element is saved
872th element is saved
873th element is saved
874th element is saved
875th element is saved
876th element is saved
877th element is saved
878th element is saved
879th element is saved
880th element is saved
881th eleme

1227th element is saved
1228th element is saved
1229th element is saved
1230th element is saved
1231th element is saved
1232th element is saved
1233th element is saved
1234th element is saved
1235th element is saved
1236th element is saved
1237th element is saved
1238th element is saved
1239th element is saved
1240th element is saved
1241th element is saved
1242th element is saved
1243th element is saved
1244th element is saved
1245th element is saved
1246th element is saved
1247th element is saved
1248th element is saved
1249th element is saved
1250th element is saved
1251th element is saved
1252th element is saved
1253th element is saved
1254th element is saved
1255th element is saved
1256th element is saved
1257th element is saved
1258th element is saved
1259th element is saved
1260th element is saved
1261th element is saved
1262th element is saved
1263th element is saved
1264th element is saved
1265th element is saved
1266th element is saved
1267th element is saved
1268th element i

1587th element is saved
1588th element is saved
1589th element is saved
1590th element is saved
1591th element is saved
1592th element is saved
1593th element is saved
1594th element is saved
1595th element is saved
1596th element is saved
1597th element is saved
1598th element is saved
1599th element is saved
1600th element is saved
1601th element is saved
1602th element is saved
1603th element is saved
1604th element is saved
1605th element is saved
1606th element is saved
1607th element is saved
1608th element is saved
1609th element is saved
1610th element is saved
1611th element is saved
1612th element is saved
1613th element is saved
1614th element is saved
1615th element is saved
1616th element is saved
1617th element is saved
1618th element is saved
1619th element is saved
1620th element is saved
1621th element is saved
1622th element is saved
1623th element is saved
1624th element is saved
1625th element is saved
1626th element is saved
1627th element is saved
1628th element i

...

2346th element is saved
2347th element is saved
2348th element is saved
2349th element is saved
2350th element is saved
2351th element is saved
2352th element is saved
2353th element is saved
2354th element is saved
2355th element is saved
2356th element is saved
2357th element is saved
2358th element is saved
2359th element is saved
2360th element is saved
2361th element is saved
2362th element is saved
2363th element is saved
2364th element is saved
2365th element is saved
2366th element is saved
2367th element is saved
2368th element is saved
2369th element is saved
2370th element is saved
2371th element is saved
2372th element is saved
2373th element is saved
2374th element is saved
2375th element is saved
2376th element is saved
2377th element is saved
2378th element is saved
2379th element is saved
2380th element is saved
2381th element is saved
2382th element is saved
2383th element is saved
2384th element is saved
2385th element is saved
2386th element is saved
2387th element i

2743th element is saved
2744th element is saved
2745th element is saved
2746th element is saved
2747th element is saved
2748th element is saved
2749th element is saved
2750th element is saved
2751th element is saved
2752th element is saved
2753th element is saved
2754th element is saved
2755th element is saved
2756th element is saved
2757th element is saved
2758th element is saved
2759th element is saved
2760th element is saved
2761th element is saved
2762th element is saved
2763th element is saved
2764th element is saved
2765th element is saved
2766th element is saved
2767th element is saved
2768th element is saved
2769th element is saved
2770th element is saved
2771th element is saved
2772th element is saved
2773th element is saved
2774th element is saved
2775th element is saved
2776th element is saved
2777th element is saved
2778th element is saved
2779th element is saved
2780th element is saved
2781th element is saved
2782th element is saved
2783th element is saved
2784th element i

3128th element is saved
3129th element is saved
3130th element is saved
3131th element is saved
3132th element is saved
3133th element is saved
3134th element is saved
3135th element is saved
3136th element is saved
3137th element is saved
3138th element is saved
3139th element is saved
3140th element is saved
3141th element is saved
3142th element is saved
3143th element is saved
3144th element is saved
3145th element is saved
3146th element is saved
3147th element is saved
3148th element is saved
3149th element is saved
3150th element is saved
3151th element is saved
3152th element is saved
3153th element is saved
3154th element is saved
3155th element is saved
3156th element is saved
3157th element is saved
3158th element is saved
3159th element is saved
3160th element is saved
3161th element is saved
3162th element is saved
3163th element is saved
3164th element is saved
3165th element is saved
3166th element is saved
3167th element is saved
3168th element is saved
3169th element i

3511th element is saved
3512th element is saved
3513th element is saved
3514th element is saved
3515th element is saved
3516th element is saved
3517th element is saved
3518th element is saved
3519th element is saved
3520th element is saved
3521th element is saved
3522th element is saved
3523th element is saved
3524th element is saved
3525th element is saved
3526th element is saved
3527th element is saved
3528th element is saved
3529th element is saved
3530th element is saved
3531th element is saved
3532th element is saved
3533th element is saved
3534th element is saved
3535th element is saved
3536th element is saved
3537th element is saved
3538th element is saved
3539th element is saved
3540th element is saved
3541th element is saved
3542th element is saved
3543th element is saved
3544th element is saved
3545th element is saved
3546th element is saved
3547th element is saved
3548th element is saved
3549th element is saved
3550th element is saved
3551th element is saved
3552th element i

3870th element is saved
3871th element is saved
3872th element is saved
3873th element is saved
3874th element is saved
3875th element is saved
3876th element is saved
3877th element is saved
3878th element is saved
3879th element is saved
3880th element is saved
3881th element is saved
3882th element is saved
3883th element is saved
3884th element is saved
3885th element is saved
3886th element is saved
3887th element is saved
3888th element is saved
3889th element is saved
3890th element is identified as No Data
3891th element is identified as No Data
3892th element is identified as No Data
3893th element is identified as No Data
3894th element is identified as No Data
3895th element is identified as No Data
3896th element is identified as No Data
3897th element is identified as No Data
3898th element is identified as No Data
3899th element is identified as No Data
3900th element is identified as No Data
3901th element is identified as No Data
3902th element is identified as No Data


In [14]:
print(len(STEO_raw_day))
print(len(STEO_raw_week))
print(len(STEO_raw_month))
print(len(STEO_raw_qtr))
print(len(STEO_raw_year))
print(len(STEO_id_dict))

0
0
1300
1295
1295
3890


In [15]:
b = pd.DataFrame(STEO_id_dict).T
b['name'] = b[0]
b['units'] = b[1]
b['frequency'] = b[2]
b.drop(columns=[0,1,2],inplace=True)
b.head()

name  \
STEO.RFCOPUS.A    Industrial Sector Generation from Residual Fue...   
STEO.OGCEPUS.A    Commercial Sector Generation from Other Gases,...   
STEO.ELDUPUS.A    Direct Use of Electricity by Commercial and In...   
STEO.EXACP_SAC.A  Retail Sales of Electricity in Transportation ...   
STEO.EXTCP_ESC.A  Retail Sales of Electricity in All Sectors, Ea...   

                                          units frequency  
STEO.RFCOPUS.A    billion kilowatthours per day    Annual  
STEO.OGCEPUS.A    billion kilowatthours per day    Annual  
STEO.ELDUPUS.A    billion kilowatthours per day    Annual  
STEO.EXACP_SAC.A  million kilowatthours per day    Annual  
STEO.EXTCP_ESC.A  million kilowatthours per day    Annual

In [16]:
b.to_pickle('STEO_id_dict.pkl')

In [18]:
STEO_raw_month_all = pd.DataFrame().join(STEO_raw_month,how='outer')
STEO_raw_qtr_all = pd.DataFrame().join(STEO_raw_qtr,how='outer')
STEO_raw_year_all = pd.DataFrame().join(STEO_raw_year,how='outer')
print(STEO_raw_month_all.shape,STEO_raw_qtr_all.shape,STEO_raw_year_all.shape)

(552, 1300) (184, 1295) (60, 1295)


In [19]:
STEO_raw_month_all.to_pickle('STEO_raw_month_all.pkl')
STEO_raw_qtr_all.to_pickle('STEO_raw_quarter_all.pkl')
STEO_raw_year_all.to_pickle('STEO_raw_year_all.pkl')